In [2]:
import pandas as pd
import os

from helpers import (
    get_data_path_for_config,
    get_combined_df,
    save_final_df_as_jsonl,
    handle_slug_column_mappings,
    set_home_type,
)

In [1]:
CONFIG_NAME = "rentals"

In [3]:
data_frames = []

slug_column_mappings = {"": "Rent"}

data_dir_path = get_data_path_for_config(CONFIG_NAME)

for filename in os.listdir(data_dir_path):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(data_dir_path, filename))
        exclude_columns = [
            "RegionID",
            "SizeRank",
            "RegionName",
            "RegionType",
            "StateName",
            "Home Type",
        ]

        cur_df["RegionName"] = cur_df["RegionName"].astype(str)

        cur_df = set_home_type(cur_df, filename)

        if "City" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Home Type",
                # City Specific
                "State",
                "Metro",
                "CountyName",
            ]
        elif "Zip" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Home Type",
                # Zip Specific
                "State",
                "City",
                "Metro",
                "CountyName",
            ]
        elif "County" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Home Type",
                # County Specific
                "State",
                "Metro",
                "StateCodeFIPS",
                "MunicipalCodeFIPS",
            ]

        data_frames = handle_slug_column_mappings(
            data_frames, slug_column_mappings, exclude_columns, filename, cur_df
        )


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "SizeRank",
        "RegionName",
        "RegionType",
        "StateName",
        "Home Type",
        "Date",
    ],
)

combined_df

In [4]:
final_df = combined_df

for index, row in final_df.iterrows():
    if row["RegionType"] == "city":
        final_df.at[index, "City"] = row["RegionName"]
    elif row["RegionType"] == "county":
        final_df.at[index, "County"] = row["RegionName"]

# coalesce State and StateName columns
final_df["State"] = final_df["State"].combine_first(final_df["StateName"])
final_df["State"] = final_df["County"].combine_first(final_df["CountyName"])

final_df = final_df.drop(columns=["StateName", "CountyName"])
final_df

RegionID  SizeRank   RegionName RegionType  \
0              66       146   Ada County     county   
1              66       146   Ada County     county   
2              66       146   Ada County     county   
3              66       146   Ada County     county   
4              66       146   Ada County     county   
...           ...       ...          ...        ...   
1258735    857850       713  Cherry Hill       city   
1258736    857850       713  Cherry Hill       city   
1258737    857850       713  Cherry Hill       city   
1258738    857850       713  Cherry Hill       city   
1258739    857850       713  Cherry Hill       city   

                          Home Type          State  \
0        all homes plus multifamily     Ada County   
1        all homes plus multifamily     Ada County   
2        all homes plus multifamily     Ada County   
3        all homes plus multifamily     Ada County   
4        all homes plus multifamily     Ada County   
...                             ...            ...   
1258735  all homes plus multifamily  Camden County   
1258736  all homes plus multifamily  Camden County   
1258737  all homes plus multifamily  Camden County   
1258738  all homes plus multifamily  Camden County   
1258739  all homes plus multifamily  Camden County   

                                               Metro  StateCodeFIPS  \
0                                     Boise City, ID           16.0   
1                                     Boise City, ID           16.0   
2                                     Boise City, ID           16.0   
3                                     Boise City, ID           16.0   
4                                     Boise City, ID           16.0   
...                                              ...            ...   
1258735  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD            NaN   
1258736  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD            NaN   
1258737  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD            NaN   
1258738  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD            NaN   
1258739  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD            NaN   

         MunicipalCodeFIPS        Date  Rent (Smoothed)  \
0                      1.0  2015-01-31       927.493763   
1                      1.0  2015-02-28       931.690623   
2                      1.0  2015-03-31       932.568601   
3                      1.0  2015-04-30       933.148134   
4                      1.0  2015-05-31       941.045724   
...                    ...         ...              ...   
1258735                NaN  2023-08-31      2291.604800   
1258736                NaN  2023-09-30      2296.188906   
1258737                NaN  2023-10-31      2292.270938   
1258738                NaN  2023-11-30      2253.417140   
1258739                NaN  2023-12-31      2280.830303   

         Rent (Smoothed) (Seasonally Adjusted)         City      County  
0                                   927.493763          NaN  Ada County  
1                                   931.690623          NaN  Ada County  
2                                   932.568601          NaN  Ada County  
3                                   933.148134          NaN  Ada County  
4                                   941.045724          NaN  Ada County  
...                                        ...          ...         ...  
1258735                            2244.961006  Cherry Hill         NaN  
1258736                            2254.213172  Cherry Hill         NaN  
1258737                            2261.540446  Cherry Hill         NaN  
1258738                            2257.956024  Cherry Hill         NaN  
1258739                            2280.830303  Cherry Hill         NaN  

[1258740 rows x 14 columns]

In [5]:
# Adjust column names
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateCodeFIPS": "State Code FIPS",
        "MunicipalCodeFIPS": "Municipal Code FIPS",
    }
)

final_df["Date"] = pd.to_datetime(final_df["Date"], format="%Y-%m-%d")

final_df

Region ID  Size Rank       Region Region Type  \
0               66        146   Ada County      county   
1               66        146   Ada County      county   
2               66        146   Ada County      county   
3               66        146   Ada County      county   
4               66        146   Ada County      county   
...            ...        ...          ...         ...   
1258735     857850        713  Cherry Hill        city   
1258736     857850        713  Cherry Hill        city   
1258737     857850        713  Cherry Hill        city   
1258738     857850        713  Cherry Hill        city   
1258739     857850        713  Cherry Hill        city   

                          Home Type          State  \
0        all homes plus multifamily     Ada County   
1        all homes plus multifamily     Ada County   
2        all homes plus multifamily     Ada County   
3        all homes plus multifamily     Ada County   
4        all homes plus multifamily     Ada County   
...                             ...            ...   
1258735  all homes plus multifamily  Camden County   
1258736  all homes plus multifamily  Camden County   
1258737  all homes plus multifamily  Camden County   
1258738  all homes plus multifamily  Camden County   
1258739  all homes plus multifamily  Camden County   

                                               Metro  State Code FIPS  \
0                                     Boise City, ID             16.0   
1                                     Boise City, ID             16.0   
2                                     Boise City, ID             16.0   
3                                     Boise City, ID             16.0   
4                                     Boise City, ID             16.0   
...                                              ...              ...   
1258735  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD              NaN   
1258736  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD              NaN   
1258737  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD              NaN   
1258738  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD              NaN   
1258739  Philadelphia-Camden-Wilmington, PA-NJ-DE-MD              NaN   

         Municipal Code FIPS       Date  Rent (Smoothed)  \
0                        1.0 2015-01-31       927.493763   
1                        1.0 2015-02-28       931.690623   
2                        1.0 2015-03-31       932.568601   
3                        1.0 2015-04-30       933.148134   
4                        1.0 2015-05-31       941.045724   
...                      ...        ...              ...   
1258735                  NaN 2023-08-31      2291.604800   
1258736                  NaN 2023-09-30      2296.188906   
1258737                  NaN 2023-10-31      2292.270938   
1258738                  NaN 2023-11-30      2253.417140   
1258739                  NaN 2023-12-31      2280.830303   

         Rent (Smoothed) (Seasonally Adjusted)         City      County  
0                                   927.493763          NaN  Ada County  
1                                   931.690623          NaN  Ada County  
2                                   932.568601          NaN  Ada County  
3                                   933.148134          NaN  Ada County  
4                                   941.045724          NaN  Ada County  
...                                        ...          ...         ...  
1258735                            2244.961006  Cherry Hill         NaN  
1258736                            2254.213172  Cherry Hill         NaN  
1258737                            2261.540446  Cherry Hill         NaN  
1258738                            2257.956024  Cherry Hill         NaN  
1258739                            2280.830303  Cherry Hill         NaN  

[1258740 rows x 14 columns]

In [7]:
save_final_df_as_jsonl(CONFIG_NAME, final_df)